## Find Bug Fixing Commits

In [171]:
import git

def find_bug_fixing_commits(repo_path, keywords, repo_name):
    repo = git.Repo(repo_path)
    bug_fixing_commits = []

    for commit in repo.iter_commits():
        for keyword in keywords:
            if keyword.lower() in commit.message.lower():
                bug_fixing_commits.append({
                    'repository': repo_name,
                    'commit_hash': commit.hexsha,
                    'keyword': keyword
                })
    
    unique_commits = []
    seen = set()

    for item in bug_fixing_commits:
        key = (item['repository'], item['commit_hash'])
        if key not in seen:
            seen.add(key)
            unique_commits.append(item)
    
    return unique_commits

In [172]:
import os
import pandas as pd

repos_path = os.path.join('data', 'repos', 'simulation')
keywords = ["fixed ", " bug", "fixes ","fix "," fix", " fixed", " fixes", "crash","solves", " resolves",
"resolves ", " issue", "issue ", "regression", "fall back", "assertion", "coverity", "reproducible",
"stack-wanted", "steps-wanted", "testcase", "failur", "fail", "npe ",
" npe", "except", "broken", "differential testing", "error", "addresssanitizer",
"hang ", " hang", "permaorange", "random orange", "intermittent", "test fix",
"steps to reproduce", "crash", "assertion", "failure", "leak", "stack trace", "heap overflow",
"freez", "str:", "problem ", " problem", " overflow", "overflow ", "avoid ",
" avoid",  "workaround ", " workaround", "break ", " break", " stop", "stop "];

all_fix_commits = []
for repo in os.listdir(repos_path):
    repo_folder_path = os.path.join(repos_path, repo)
    
    if os.path.isdir(repo_folder_path):    
        print("Getting fix commits of ", repo)
        bug_fixing_commits = find_bug_fixing_commits(repo_folder_path, keywords, repo)
        all_fix_commits.extend(bug_fixing_commits)

        
df = pd.DataFrame(all_fix_commits)
print(df)

Getting fix commits of  adf-sample-agent-java
Getting fix commits of  aerie
Getting fix commits of  AgentWorkbench
Getting fix commits of  amod
Getting fix commits of  amodeus
Getting fix commits of  annotation-simulator
Getting fix commits of  AutoInteraction-Library
Getting fix commits of  Black-Scholes-Option-Pricing-Model
Getting fix commits of  BoomChess-Android
Getting fix commits of  cas
Getting fix commits of  cloudsimplus
Getting fix commits of  cloudsimplus-automation
Getting fix commits of  cloudsimplus-examples
Getting fix commits of  cloudsimsdn
Getting fix commits of  computer_kurzweil
Getting fix commits of  DesSim
Getting fix commits of  ecosim
Getting fix commits of  end-game
Getting fix commits of  eqasim-java
Getting fix commits of  EVLib
Getting fix commits of  Evolving-Protozoa
Getting fix commits of  farmsim
Getting fix commits of  finmath-lib
Getting fix commits of  FlockingSimulation
Getting fix commits of  gama
Getting fix commits of  gips
Getting fix commits o

## Get Bug Inducing Commits

In [40]:
from pydriller import Repository, Git

import os

repos_path = os.path.join('data', 'repos', 'simulation')

def get_values_by_key(list_of_dicts, key):
    return [d[key] for d in list_of_dicts if key in d]

all_inducing_commits = []

for repo in os.listdir(repos_path):
    repo_folder_path = os.path.join(repos_path, repo)
    if os.path.isdir(repo_folder_path):
        print("Getting inducing commits for ", repo)
        repository = Git(repo_folder_path)
        
        fixed_commits = df[df['repository'] == repo]
        fixed_commit_list = fixed_commits['commit_hash'].tolist()
        for fixed_commit in fixed_commit_list:
            
            commit = repository.get_commit(fixed_commit)
            prev_commits = repository.get_commits_last_modified_lines(commit)
            
            for file in prev_commits.keys():
                file_commits = prev_commits[file]
                hashes = list(file_commits)
                
                for commit_hash in hashes:
                    all_inducing_commits.append({
                    'repository': repo,
                    'fixing_commit': fixed_commit,
                    'fixing_commit_date': repository.get_commit(fixed_commit).committer_date,
                    'inducing_commit':commit_hash,
                    'inducing_commit_date': repository.get_commit(commit_hash).committer_date,
                    'file': file,
                    'keyword': fixed_commits[fixed_commits['commit_hash']==fixed_commit]['keyword'].tolist()[0]
                    })

Getting inducing commits for  adf-sample-agent-java
Getting inducing commits for  aerie
Getting inducing commits for  AgentWorkbench
Getting inducing commits for  amod
Getting inducing commits for  amodeus
Getting inducing commits for  annotation-simulator
Getting inducing commits for  AutoInteraction-Library
Getting inducing commits for  Black-Scholes-Option-Pricing-Model
Getting inducing commits for  BoomChess-Android
Getting inducing commits for  cas
Getting inducing commits for  cloudsimplus
Getting inducing commits for  cloudsimplus-automation
Getting inducing commits for  cloudsimplus-examples
Getting inducing commits for  cloudsimsdn
Getting inducing commits for  computer_kurzweil
Getting inducing commits for  DesSim
Getting inducing commits for  ecosim
Getting inducing commits for  end-game
Getting inducing commits for  eqasim-java
Getting inducing commits for  EVLib
Getting inducing commits for  Evolving-Protozoa
Getting inducing commits for  farmsim
Getting inducing commits f

In [43]:
inducing_df = pd.DataFrame(all_inducing_commits)
inducing_df = inducing_df.drop_duplicates()
inducing_df.to_csv('inducing_df.csv')
inducing_df

repository                             fixing_commit  \
0       adf-sample-agent-java  d42692cbe8be18793d0a4fd7cddb7a6ce29d53a8   
1       adf-sample-agent-java  d3631db88bd15c8f7a6048207a3e6fdd0f336a02   
2       adf-sample-agent-java  d3631db88bd15c8f7a6048207a3e6fdd0f336a02   
3       adf-sample-agent-java  d3631db88bd15c8f7a6048207a3e6fdd0f336a02   
4       adf-sample-agent-java  d3631db88bd15c8f7a6048207a3e6fdd0f336a02   
...                       ...                                       ...   
169976              workcraft  8af53c2871d9c5489eb293a2e5fd647cb41f2ca6   
169977              workcraft  8af53c2871d9c5489eb293a2e5fd647cb41f2ca6   
169978              workcraft  ce741bb20f73fd4c7aaeba66efb2aa4092189b81   
169979              workcraft  ce741bb20f73fd4c7aaeba66efb2aa4092189b81   
169980              workcraft  ce741bb20f73fd4c7aaeba66efb2aa4092189b81   

               fixing_commit_date                           inducing_commit  \
0       2022-10-03 08:41:08+02:00  ed2a18fd5c0c263d9fe27a1c442244ad0a649590   
1       2018-10-12 17:23:33+02:00  a3e60f117511ac957c5f83f45cc279262272f4aa   
2       2018-10-12 17:23:33+02:00  8d58c5c79766df9ea34fe3ea32356bbd0e90dc58   
3       2018-10-12 17:23:33+02:00  193f33f4e2ccb5e7e7bc5f979048502e9495d4fd   
4       2018-10-12 17:23:33+02:00  35f3d2b9f2a069238e3fc3c65e838a74da0ff4cd   
...                           ...                                       ...   
169976  2009-01-14 10:48:21+00:00  9104befbe5fce0e8dfbb65bcfc178900219a5448   
169977  2009-01-14 10:48:21+00:00  4e791baeafa80ce7fda92daa2338c1b0f0c57685   
169978  2009-01-05 21:28:10+00:00  09b84f0c5c782209c0225f7287347623cb8e171f   
169979  2009-01-05 21:28:10+00:00  09b84f0c5c782209c0225f7287347623cb8e171f   
169980  2009-01-05 21:28:10+00:00  09b84f0c5c782209c0225f7287347623cb8e171f   

             inducing_commit_date  \
0       2022-01-11 21:56:46+01:00   
1       2016-12-08 21:15:59+09:00   
2       2016-09-20 12:31:12+09:00   
3       2015-11-26 07:35:10+09:00   
4       2015-12-02 13:42:29+09:00   
...                           ...   
169976  2008-12-03 19:06:23+00:00   
169977  2008-12-12 23:15:24+00:00   
169978  2009-01-05 20:58:27+00:00   
169979  2009-01-05 20:58:27+00:00   
169980  2009-01-05 20:58:27+00:00   

                                                  file keyword  
0                                    config\module.cfg  fixes   
1                                            .build.sh  fixed   
2                                   .update-library.sh  fixed   
3                                   .update-library.sh  fixed   
4                                   .update-library.sh  fixed   
...                                                ...     ...  
169976  workcraft\dom\visual\VisualComponentGroup.java  fixed   
169977  workcraft\dom\visual\VisualComponentGroup.java  fixed   
169978                    workcraft\gui\Coloriser.java  fixed   
169979        workcraft\plugins\petri\VisualPlace.java  fixed   
169980   workcraft\plugins\petri\VisualTransition.java  fixed   

[169981 rows x 7 columns]

## Detect Code Smells

In [3]:
import pandas as pd
inducing_df = pd.read_csv('inducing_df.csv')
inducing_df['inducing_commit_date'] = pd.to_datetime(inducing_df['inducing_commit_date'], utc=True)
inducing_df['fixing_commit_date'] = pd.to_datetime(inducing_df['fixing_commit_date'], utc=True)
# inducing_df = inducing_df.sort_values(by='inducing_commit_date')
# inducing_df = inducing_df.drop_duplicates(subset=['repository', 'fixing_commit', 'file'], keep='first')
inducing_df

Unnamed: 0             repository  \
0                0  adf-sample-agent-java   
1                1  adf-sample-agent-java   
2                2  adf-sample-agent-java   
3                3  adf-sample-agent-java   
4                4  adf-sample-agent-java   
...            ...                    ...   
169976      169976              workcraft   
169977      169977              workcraft   
169978      169978              workcraft   
169979      169979              workcraft   
169980      169980              workcraft   

                                   fixing_commit        fixing_commit_date  \
0       d42692cbe8be18793d0a4fd7cddb7a6ce29d53a8 2022-10-03 06:41:08+00:00   
1       d3631db88bd15c8f7a6048207a3e6fdd0f336a02 2018-10-12 15:23:33+00:00   
2       d3631db88bd15c8f7a6048207a3e6fdd0f336a02 2018-10-12 15:23:33+00:00   
3       d3631db88bd15c8f7a6048207a3e6fdd0f336a02 2018-10-12 15:23:33+00:00   
4       d3631db88bd15c8f7a6048207a3e6fdd0f336a02 2018-10-12 15:23:33+00:00   
...                                          ...                       ...   
169976  8af53c2871d9c5489eb293a2e5fd647cb41f2ca6 2009-01-14 10:48:21+00:00   
169977  8af53c2871d9c5489eb293a2e5fd647cb41f2ca6 2009-01-14 10:48:21+00:00   
169978  ce741bb20f73fd4c7aaeba66efb2aa4092189b81 2009-01-05 21:28:10+00:00   
169979  ce741bb20f73fd4c7aaeba66efb2aa4092189b81 2009-01-05 21:28:10+00:00   
169980  ce741bb20f73fd4c7aaeba66efb2aa4092189b81 2009-01-05 21:28:10+00:00   

                                 inducing_commit      inducing_commit_date  \
0       ed2a18fd5c0c263d9fe27a1c442244ad0a649590 2022-01-11 20:56:46+00:00   
1       a3e60f117511ac957c5f83f45cc279262272f4aa 2016-12-08 12:15:59+00:00   
2       8d58c5c79766df9ea34fe3ea32356bbd0e90dc58 2016-09-20 03:31:12+00:00   
3       193f33f4e2ccb5e7e7bc5f979048502e9495d4fd 2015-11-25 22:35:10+00:00   
4       35f3d2b9f2a069238e3fc3c65e838a74da0ff4cd 2015-12-02 04:42:29+00:00   
...                                          ...                       ...   
169976  9104befbe5fce0e8dfbb65bcfc178900219a5448 2008-12-03 19:06:23+00:00   
169977  4e791baeafa80ce7fda92daa2338c1b0f0c57685 2008-12-12 23:15:24+00:00   
169978  09b84f0c5c782209c0225f7287347623cb8e171f 2009-01-05 20:58:27+00:00   
169979  09b84f0c5c782209c0225f7287347623cb8e171f 2009-01-05 20:58:27+00:00   
169980  09b84f0c5c782209c0225f7287347623cb8e171f 2009-01-05 20:58:27+00:00   

                                                  file keyword  
0                                    config\module.cfg  fixes   
1                                            .build.sh  fixed   
2                                   .update-library.sh  fixed   
3                                   .update-library.sh  fixed   
4                                   .update-library.sh  fixed   
...                                                ...     ...  
169976  workcraft\dom\visual\VisualComponentGroup.java  fixed   
169977  workcraft\dom\visual\VisualComponentGroup.java  fixed   
169978                    workcraft\gui\Coloriser.java  fixed   
169979        workcraft\plugins\petri\VisualPlace.java  fixed   
169980   workcraft\plugins\petri\VisualTransition.java  fixed   

[169981 rows x 8 columns]

In [4]:
def filter_dates(group, col_name):
    filtered_rows = []
    last_date = None
    for index, row in group.iterrows():
        if last_date is None or abs((row[col_name] - last_date).days) >= 28:
            filtered_rows.append(row)
            last_date = row[col_name]
    return pd.DataFrame(filtered_rows)

inducing_df = inducing_df.groupby('repository').apply(filter_dates, col_name='inducing_commit_date').reset_index(drop=True)
inducing_df = inducing_df.groupby('repository').apply(filter_dates, col_name='fixing_commit_date').reset_index(drop=True)
inducing_df

Unnamed: 0      repository                             fixing_commit  \
0           6562  AgentWorkbench  44462f6e93288995e8b43e1bc32ccb08e1a05c57   
1           6565  AgentWorkbench  e1cdeb68b52358cfcc839c8d39954da52f2449a9   
2           6578  AgentWorkbench  2333f9e8b76dc7100b05b4dd2c3c23b853a6da60   
3           6586  AgentWorkbench  deb51dc4b1d766fb6367557b9748709cb2b31f2b   
4           6599  AgentWorkbench  fc65f2dde8492597514ec179953c60ecf13a41ee   
...          ...             ...                                       ...   
1291      169474       workcraft  3108bd24e1544221a04157ddfd685cd4893a5bb6   
1292      169484       workcraft  c31415990c0b499c9b07efd8e1f33aaa20bad223   
1293      169501       workcraft  721d53214c6a8acd84fc71c05e2f6534a2a65177   
1294      169561       workcraft  1eeab1876622b1dd1b57aae6d065599f9f49caa3   
1295      169833       workcraft  489825b8975e361c646c881d6759882ab3a72b57   

            fixing_commit_date                           inducing_commit  \
0    2023-10-10 08:58:04+00:00  c2510d8be0260eb97c960bf1fe24ebaf5f833dab   
1    2023-08-21 14:15:19+00:00  8f0ed077e2a79a838d2e1a2105569f318f1a8124   
2    2023-07-16 14:00:52+00:00  68ee6125a9bdedbcc628247e8326143c071591a9   
3    2023-04-20 16:03:58+00:00  a581543ccd53828ea38e404a2af6cb16a8e59da1   
4    2023-03-14 11:42:28+00:00  65438f8429cbe0153ece9f0c51ddf5bb5595275b   
...                        ...                                       ...   
1291 2009-07-12 22:46:56+00:00  23881e2d8339655c8aaad42efff0524194299204   
1292 2009-05-16 08:28:05+00:00  8d9018e93a6217c3ff9db28cbf0e01008bafca44   
1293 2009-03-25 09:29:37+00:00  5096f698a98a707c12190fee9fe0168763ed5a18   
1294 2009-02-25 13:56:34+00:00  ac849ca420ad8076f30a3809d708278ec4bf6f3f   
1295 2009-01-25 23:19:43+00:00  5cab9dbb682e35951e492d1758275b618414e9df   

          inducing_commit_date  \
0    2023-01-08 16:54:15+00:00   
1    2023-04-20 16:00:38+00:00   
2    2019-09-26 14:02:54+00:00   
3    2022-08-23 15:08:11+00:00   
4    2022-08-02 10:10:51+00:00   
...                        ...   
1291 2009-02-21 20:23:16+00:00   
1292 2008-07-08 15:57:32+00:00   
1293 2008-08-10 08:54:36+00:00   
1294 2008-12-06 20:57:13+00:00   
1295 2008-07-14 10:55:39+00:00   

                                                   file   keyword  
0     eclipseProjects\de.enflexit.awb\bundles\de.enf...    fixed   
1     eclipseProjects\de.enflexit.awb\bundles\org.aw...    fixed   
2     eclipseProjects\de.enflexit.awb\bundles\org.aw...  problem   
3     eclipseProjects\de.enflexit.awb\bundles\de.enf...      stop  
4     eclipseProjects\de.enflexit.awb\bundles\de.enf...    fixed   
...                                                 ...       ...  
1291              workcraft\dom\visual\VisualModel.java    fixed   
1292                             workcraft\gui\LAF.java   problem  
1293                       workcraft\dom\MathModel.java    break   
1294                workcraft\gui\CreateWorkDialog.java    fixed   
1295                       workcraft\dom\MathModel.java    fixed   

[1296 rows x 8 columns]

In [95]:
tdf_fix = inducing_df.drop_duplicates(subset=['repository', 'fixing_commit'])
tdf_ind = inducing_df.drop_duplicates(subset=['repository', 'inducing_commit'])

In [96]:
print(len(tdf_fix), len(tdf_ind))

11330 22623


In [97]:
tdf_fix = tdf_fix.groupby('repository').apply(filter_dates, col_name='fixing_commit_date').reset_index(drop=True)
tdf_ind = tdf_ind.groupby('repository').apply(filter_dates, col_name='inducing_commit_date').reset_index(drop=True)

In [99]:
print(len(tdf_fix), len(tdf_ind))
pd.merge(tdf_fix, tdf_ind)

1375 16285


Unnamed: 0      repository                             fixing_commit  \
0          6562  AgentWorkbench  44462f6e93288995e8b43e1bc32ccb08e1a05c57   
1          6565  AgentWorkbench  e1cdeb68b52358cfcc839c8d39954da52f2449a9   
2          6578  AgentWorkbench  2333f9e8b76dc7100b05b4dd2c3c23b853a6da60   
3          6586  AgentWorkbench  deb51dc4b1d766fb6367557b9748709cb2b31f2b   
4          6654  AgentWorkbench  35634ef0e7413658a77fa67b9a45057b77c80a6a   
..          ...             ...                                       ...   
478      165840       workcraft  3be6b7ca948d406e21910a03dd71ceeca1bea6cf   
479      165852       workcraft  9ba4476faf0ad0d6d70562f9e4c75f8e5cbcd4f1   
480      165943       workcraft  9216feb585adf8794cbb21300f15aa6263cf2056   
481      166301       workcraft  ef6b15b6d0a47512d60971bf53f4d58653b5f343   
482      167939       workcraft  a9265205483a19f56b766057c29141e159f7c866   

           fixing_commit_date                           inducing_commit  \
0   2023-10-10 08:58:04+00:00  c2510d8be0260eb97c960bf1fe24ebaf5f833dab   
1   2023-08-21 14:15:19+00:00  8f0ed077e2a79a838d2e1a2105569f318f1a8124   
2   2023-07-16 14:00:52+00:00  68ee6125a9bdedbcc628247e8326143c071591a9   
3   2023-04-20 16:03:58+00:00  a581543ccd53828ea38e404a2af6cb16a8e59da1   
4   2022-10-12 10:20:26+00:00  ed115d32a1f202ba873e692d5c06bba3a4dc3bf7   
..                        ...                                       ...   
478 2015-01-20 16:08:50+00:00  871fb61400fbbc6835fa2d903d5ed7470f661bcf   
479 2014-12-14 10:25:50+00:00  5f4417daa9195686764e3cedb03012939e668c65   
480 2014-11-14 23:43:09+00:00  43948490f0059fef6b2935e582a3c4ecff28527c   
481 2014-08-06 15:33:46+00:00  cb57bc73f5605c48dbfc92f4befbf3fd67deb3fb   
482 2011-05-08 18:04:59+00:00  3d268ddbbafb639d88d39f5e4d99936fefce44b6   

         inducing_commit_date  \
0   2023-01-08 16:54:15+00:00   
1   2023-04-20 16:00:38+00:00   
2   2019-09-26 14:02:54+00:00   
3   2022-08-23 15:08:11+00:00   
4   2017-08-24 15:59:55+00:00   
..                        ...   
478 2014-04-03 17:30:41+00:00   
479 2014-05-06 09:15:57+00:00   
480 2014-07-11 16:22:02+00:00   
481 2009-02-22 16:12:29+00:00   
482 2010-09-20 07:55:38+00:00   

                                                  file   keyword  
0    eclipseProjects\de.enflexit.awb\bundles\de.enf...    fixed   
1    eclipseProjects\de.enflexit.awb\bundles\org.aw...    fixed   
2    eclipseProjects\de.enflexit.awb\bundles\org.aw...  problem   
3    eclipseProjects\de.enflexit.awb\bundles\de.enf...      stop  
4    eclipseProjects\de.enflexit.awb\bundles\de.enf...       bug  
..                                                 ...       ...  
478  STGPlugin\src\org\workcraft\plugins\stg\LabelP...      fix   
479  SONPlugin\src\org\workcraft\plugins\son\elemen...      fix   
480  MpsatPlugin\src\org\workcraft\plugins\mpsat\gu...    fixes   
481  WorkcraftCore\src\org\workcraft\gui\graph\tool...    fixes   
482                             BalsaPlugin\.classpath    fixed   

[483 rows x 8 columns]

In [5]:
from git import Repo,GitCommandError
import analyze_code
import shutil
repos_path = os.path.join('data', 'repos', 'simulation')

repo_path = os.path.join('data', 'repos', 'simulation')
bug_fix_path = os.path.join('data', 'mining', 'fixed', 'simulation')
bug_inducing_path = os.path.join('data', 'mining', 'inducing', 'simulation')
dj_file_path = os.path.join('apps', 'DJ', 'DesigniteJava.jar')


for repo in os.listdir(repos_path):
    repo_folder_path = os.path.join(repos_path, repo)
    
    if os.path.isdir(repo_folder_path):
        temp_df =  inducing_df[inducing_df['repository'] == repo]
        
        # BUG FIXING COMMITS
        #################################################################
        print("Analyzing bug fixing commits of ", repo)
        resolved_commit_hashes = temp_df['fixing_commit'].unique().tolist()
        
        fix_repo_path = os.path.join(bug_fix_path, repo)
        if not os.path.exists(fix_repo_path):
            os.makedirs(fix_repo_path)
        
        count = 0
        
        # check if folder is already analyzed
        if os.path.isfile(os.path.join(fix_repo_path, "completed.txt")):
            continue

        repository = Repo(repo_folder_path)
        head_commit = repository.head.commit.hexsha

        for commit in resolved_commit_hashes:
            print("Analyzing the ", count, "th commit of ", repo)
            try:
                repository.git.reset('--hard', commit)
            except GitCommandError:
                print("encounter error while resetting, skipping commit")
                continue
            result_path = os.path.join(fix_repo_path, repo+'_'+commit)
            analyze_code.analyze_repo(repo_folder_path, result_path, os.path.abspath(dj_file_path))
            commit_info = repository.commit(commit)
            with open(os.path.join(result_path,'commit_date.txt'), 'w') as file:
                file.write(str(commit_info.authored_datetime))


            if os.path.isfile(os.path.join(result_path, "MethodMetrics.csv")):
                # do a check to see if we get metrics and stop 
                adf = pd.read_csv(os.path.join(result_path, "MethodMetrics.csv"))
                if adf.empty:
                    print("No results found for ", repo, " at ", count, "th step")
                    shutil.rmtree(result_path)
                    count+=1
                    continue

            count+=1

        # analyze_code.analyze_repo_multi(repo_path, folder_path, os.path.abspath(dj_file_path), main_branch)

        # set a file as a merker to indicate its finished analyzing
        end_file = open(os.path.join(fix_repo_path, "completed.txt"), 'w')
        end_file.write("COMPLETED")
        end_file.close()
        print("Finished Analysis of ", repo)
        repository.git.reset('--hard', head_commit)
        print("Resetting repo back to head")
        
        

Analyzing bug fixing commits of  adf-sample-agent-java
Analyzing bug fixing commits of  aerie
Analyzing bug fixing commits of  AgentWorkbench
Analyzing bug fixing commits of  amod
Analyzing bug fixing commits of  amodeus
Analyzing bug fixing commits of  annotation-simulator
Analyzing bug fixing commits of  AutoInteraction-Library
Analyzing bug fixing commits of  Black-Scholes-Option-Pricing-Model
Analyzing bug fixing commits of  BoomChess-Android
Analyzing bug fixing commits of  cas
Analyzing bug fixing commits of  cloudsimplus
Analyzing bug fixing commits of  cloudsimplus-automation
Analyzing bug fixing commits of  cloudsimplus-examples
Analyzing bug fixing commits of  cloudsimsdn
Analyzing bug fixing commits of  computer_kurzweil
Analyzing bug fixing commits of  DesSim
Analyzing bug fixing commits of  ecosim
Analyzing bug fixing commits of  end-game
Analyzing bug fixing commits of  eqasim-java
Analyzing bug fixing commits of  EVLib
Analyzing bug fixing commits of  Evolving-Protozoa
A

Analyzingdata\repos\simulation\finmath-lib ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  35 th commit of  finmath-lib
Analyzingdata\repos\simulation\finmath-lib ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  finmath-lib  at  35 th step
Analyzing the  36 th commit of  finmath-lib
Analyzingdata\repos\simulation\finmath-lib ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  finmath-lib  at  36 th step
Analyzing the  37 th commit of  finmath-lib
Analyzingdata\repos\simulation\finmath-lib ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  finmath-lib  at  37 th step
Analyzing the  38 th commit of  finmath-lib
Analyzingdata\repos\simulation\finmath-lib ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  finmath-lib  at  38 th step
Analyzing the  39 th commit of  finmath

done analyzing.
Analyzing the  7 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  8 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  9 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  10 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  11 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  12 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  13 th commit of  gips
Analyzingdata\repos\simulation\gips ...
Attempting compi

Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  15 th step
Analyzing the  16 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  16 th step
Analyzing the  17 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  17 th step
Analyzing the  18 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  18 th step
Analyzing the  19 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  19 th step
Analyzing the  20 th commit of 

Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  56 th step
Analyzing the  57 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  57 th step
Analyzing the  58 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  58 th step
Analyzing the  59 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  59 th step
Analyzing the  60 th commit of  mars-sim
Analyzingdata\repos\simulation\mars-sim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
No results found for  mars-sim  at  60 th step
Analyzing the  61 th commit of 

...

Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  72 th step
Analyzing the  73 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  73 th step
Analyzing the  74 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  74 th step
Analyzing the  75 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  75 th step
Analyzing the  76 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  76 th step
Analyzing the  77 th commit of  syn

Analyzing ...
done analyzing.
Analyzing the  19 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  20 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  21 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  22 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  23 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  24 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  25 th commit of  varsim
Analyzingdata\repos\simul

Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  27 th step
Analyzing the  28 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  28 th step
Analyzing the  29 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  29 th step
Analyzing the  30 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  30 th step
Analyzing the  31 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  31 

done analyzing.
No results found for  workcraft  at  66 th step
Analyzing the  67 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  67 th step
Analyzing the  68 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  68 th step
Analyzing the  69 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  69 th step
Analyzing the  70 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  70 th step
Analyzing the  71 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attemptin

done analyzing.
Analyzing the  107 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  108 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  109 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  110 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  111 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  112 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  113 th co

In [6]:
from git import Repo,GitCommandError
import analyze_code
import shutil
import os

repos_path = os.path.join('data', 'repos', 'simulation')
bug_fix_path = os.path.join('data', 'mining', 'fixed', 'simulation')
bug_inducing_path = os.path.join('data', 'mining', 'inducing', 'simulation')
dj_file_path = os.path.join('apps', 'DJ', 'DesigniteJava.jar')


for repo in os.listdir(repos_path):
    repo_folder_path = os.path.join(repos_path, repo)
    
    if os.path.isdir(repo_folder_path):
        temp_df =  inducing_df[inducing_df['repository'] == repo]
        
        # BUG INDUCING COMMITS
        #################################################################
        
        print("Analyzing bug inducing commits of ", repo)
        inducing_commit_hashes = temp_df['inducing_commit'].unique().tolist()
        
        induce_repo_path = os.path.join(bug_inducing_path, repo)
        if not os.path.exists(induce_repo_path):
            os.makedirs(induce_repo_path)
        
        count = 0
        
        # check if folder is already analyzed
        if os.path.isfile(os.path.join(induce_repo_path, "completed.txt")):
            continue

        repository = Repo(repo_folder_path)
        head_commit = repository.head.commit.hexsha

        for commit in inducing_commit_hashes:
            result_path = os.path.join(induce_repo_path, repo+'_'+commit)
            if os.path.isdir(result_path):
                print(result_path, " Already exists, no need to analyze")
                count += 1
                continue
            
            print("Analyzing the ", count, "th commit of ", repo)
            
            try:
                repository.git.reset('--hard', commit)
            except GitCommandError:
                print("encounter error while resetting, skipping commit")
                continue
                
            analyze_code.analyze_repo(repo_folder_path, result_path, os.path.abspath(dj_file_path))
            commit_info = repository.commit(commit)
            with open(os.path.join(result_path,'commit_date.txt'), 'w') as file:
                file.write(str(commit_info.authored_datetime))


            if os.path.isfile(os.path.join(result_path, "MethodMetrics.csv")):
                # do a check to see if we get metrics and stop 
                adf = pd.read_csv(os.path.join(result_path, "MethodMetrics.csv"))
                if adf.empty:
                    print("No results found for ", repo, " at ", count, "th step")
                    shutil.rmtree(result_path)
                    continue

            count+=1

        # analyze_code.analyze_repo_multi(repo_path, folder_path, os.path.abspath(dj_file_path), main_branch)

        # set a file as a merker to indicate its finished analyzing
        end_file = open(os.path.join(induce_repo_path, "completed.txt"), 'w')
        end_file.write("COMPLETED")
        end_file.close()
        print("Finished Analysis of ", repo)
        repository.git.reset('--hard', head_commit)

Analyzing bug inducing commits of  adf-sample-agent-java
Analyzing the  0 th commit of  adf-sample-agent-java
Analyzingdata\repos\simulation\adf-sample-agent-java ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
Analyzing the  1 th commit of  adf-sample-agent-java
Analyzingdata\repos\simulation\adf-sample-agent-java ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  2 th commit of  adf-sample-agent-java
Analyzingdata\repos\simulation\adf-sample-agent-java ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  3 th commit of  adf-sample-agent-java
Analyzingdata\repos\simulation\adf-sample-agent-java ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  4 th commit of  adf-sample-agent-java
Analyzingdata\repos\simulation\adf-sample-agent-java ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  5 th commit of 

Analyzing ...
done analyzing.
Analyzing the  40 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  41 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  42 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  43 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  44 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  45 th commit of  aerie
Analyzingdata\repos\simulation\aerie ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  46 th commit of  aerie
Analyzingdata\repos\simulation\aerie .

done analyzing.
No results found for  AgentWorkbench  at  0 th step
Analyzing the  0 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  1 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  1 th step
Analyzing the  1 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  1 th step
Analyzing the  1 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  1 th step
Analyzing the  1 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempti

done analyzing.
No results found for  AgentWorkbench  at  6 th step
Analyzing the  6 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  6 th step
Analyzing the  6 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  6 th step
Analyzing the  6 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  6 th step
Analyzing the  6 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  AgentWorkbench  at  6 th step
Analyzing the  6 th commit of  AgentWorkbench
Analyz

Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  12 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  13 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  14 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  15 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  16 th commit of  AgentWorkbench
Analyzingdata\repos\simulation\AgentWorkbench ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  17 th commit of  A

...

done analyzing.
Analyzing the  55 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
Analyzing the  56 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
Analyzing the  57 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
Analyzing the  58 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  synthea  at  58 th step
Analyzing the  58 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
Analyzing the  59 th commit of  synthea
Analyzingdata\repos\simulation\synthea ...
Attempting compilation...
Found build.gradle
Analyzing ...
done anal

done analyzing.
Analyzing the  8 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  9 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  10 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  11 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  12 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  13 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...
Attempting compilation...
Found pom.xml
Analyzing ...
done analyzing.
Analyzing the  14 th commit of  varsim
Analyzingdata\repos\simulation\varsim ...

Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  0 th step
Analyzing the  0 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  0 th step
Analyzing the  0 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  0 th step
Analyzing the  0 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  0 th step
Analyzing the  0 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  workcraft  at  0 th step
Anal

Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  1 th step
Analyzing the  1 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  1 th step
Analyzing the  1 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  workcraft  at  1 th step
Analyzing the  1 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Found build.gradle
Analyzing ...
done analyzing.
No results found for  workcraft  at  1 th step
Analyzing the  1 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
No results found for  workcraft  at  1 th step
Analyzi

done analyzing.
Analyzing the  16 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  17 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  18 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  19 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  20 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  21 th commit of  workcraft
Analyzingdata\repos\simulation\workcraft ...
Attempting compilation...
Did not compile
Analyzing ...
done analyzing.
Analyzing the  22 th commit of

## Aggregate Smell Analysis 

In [171]:
import os

fixed_path = os.path.join('data', 'mining','fixed', 'simulation')
inducing_path = os.path.join('data', 'mining','inducing', 'simulation')

# for row in inducing_df.iterrows():
#     print(row)
#     break

imp_agg = pd.DataFrame(columns=['Project','Package', 'Type','Method', 'Smell','commit'])
des_agg = pd.DataFrame(columns=['Project','Package', 'Type', 'Smell', 'commit'])
arch_agg = pd.DataFrame(columns=['Project', 'Package', 'Smell', 'commit'])
        
for repo in os.listdir(fixed_path):
    repo_path = os.path.join(fixed_path, repo)
    
    print("Analyzing repo ", repo)
    
    sub_imp_agg = pd.DataFrame(columns=['Project','Package', 'Type','Method', 'Smell', 'commit'])
    sub_des_agg = pd.DataFrame(columns=['Project','Package', 'Type', 'Smell', 'commit'])
    sub_arch_agg = pd.DataFrame(columns=['Project', 'Package', 'Smell', 'commit'])
    for subfolder in os.listdir(repo_path):
        subfolder_path = os.path.join(repo_path, subfolder)
        
        if os.path.isdir(subfolder_path):
            commit = subfolder_path.split('_')[1]
            print('Analyzing commit ', commit, ' of ', repo)
            
            metrics_path = os.path.join(subfolder_path, 'MethodMetrics.csv')
            implementaion_path = os.path.join(subfolder_path, 'ImplementationSmells.csv')
            design_path = os.path.join(subfolder_path, 'DesignSmells.csv')
            arch_path = os.path.join(subfolder_path, 'ArchitectureSmells.csv')
            
            implementation = pd.read_csv(implementaion_path, on_bad_lines='warn')
            implementation = implementation.drop_duplicates()
            implementation = implementation.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Type Name': 'Type',
                'Method Name': 'Method',
                'Implementation Smell': 'Smell'
            })
            implementation['commit'] = commit;
            
            design = pd.read_csv(design_path, on_bad_lines='warn')
            design = design.drop_duplicates()
            
            design = design.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Type Name': 'Type',
                'Design Smell': 'Smell'
            })
            design['commit'] = commit;
            
            architecture = pd.read_csv(arch_path, on_bad_lines='warn')
            architecture = architecture.drop_duplicates()
            
            architecture = architecture.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Architecture Smell': 'Smell'
            })
            architecture['commit'] = commit;
            
            sub_imp_agg = pd.concat([sub_imp_agg, implementation])
            sub_des_agg = pd.concat([sub_des_agg, design])
            sub_arch_agg = pd.concat([sub_arch_agg, architecture])
            
            sub_imp_agg = sub_imp_agg.drop_duplicates()
            sub_des_agg = sub_des_agg.drop_duplicates()
            sub_arch_agg = sub_arch_agg.drop_duplicates()

        imp_agg = pd.concat([sub_imp_agg, imp_agg])
        des_agg = pd.concat([sub_des_agg, des_agg])
        arch_agg = pd.concat([sub_arch_agg, arch_agg])


Analyzing repo  adf-sample-agent-java
Analyzing commit  25425d84a4e8468ab8eda39fade794de7435066f  of  adf-sample-agent-java


Skipping line 14: expected 5 fields, saw 6
Skipping line 24: expected 5 fields, saw 6
Skipping line 26: expected 5 fields, saw 6
Skipping line 29: expected 5 fields, saw 6
Skipping line 35: expected 5 fields, saw 6
Skipping line 37: expected 5 fields, saw 6
Skipping line 40: expected 5 fields, saw 6
Skipping line 43: expected 5 fields, saw 6
Skipping line 45: expected 5 fields, saw 6
Skipping line 57: expected 5 fields, saw 6
Skipping line 63: expected 5 fields, saw 6
Skipping line 66: expected 5 fields, saw 6



Analyzing commit  3e3e687d8af5ea5649a8132e9c6618837331f9a1  of  adf-sample-agent-java
Analyzing commit  43761337ea5d25893ebd25222869826c84b562da  of  adf-sample-agent-java


Skipping line 4: expected 5 fields, saw 6
Skipping line 14: expected 5 fields, saw 6
Skipping line 17: expected 5 fields, saw 6
Skipping line 21: expected 5 fields, saw 6

Skipping line 14: expected 5 fields, saw 6
Skipping line 21: expected 5 fields, saw 6
Skipping line 23: expected 5 fields, saw 6
Skipping line 26: expected 5 fields, saw 6
Skipping line 29: expected 5 fields, saw 6
Skipping line 31: expected 5 fields, saw 6
Skipping line 34: expected 5 fields, saw 6
Skipping line 36: expected 5 fields, saw 6
Skipping line 43: expected 5 fields, saw 6



Analyzing commit  6d26a9cd292e738b20cea2adcf23210fbee3c33c  of  adf-sample-agent-java
Analyzing commit  84598cff8c2498e56d6a845bea9597f5e281f356  of  adf-sample-agent-java
Analyzing commit  a84eb7bb8e1d7f7baf0248b5cfef25202ff8b7a5  of  adf-sample-agent-java


...

Skipping line 11: expected 5 fields, saw 6
Skipping line 13: expected 5 fields, saw 6
Skipping line 15: expected 5 fields, saw 6
Skipping line 21: expected 5 fields, saw 6
Skipping line 83: expected 5 fields, saw 6
Skipping line 90: expected 5 fields, saw 6
Skipping line 93: expected 5 fields, saw 6
Skipping line 97: expected 5 fields, saw 6
Skipping line 103: expected 5 fields, saw 6
Skipping line 106: expected 5 fields, saw 6
Skipping line 109: expected 5 fields, saw 6
Skipping line 114: expected 5 fields, saw 6
Skipping line 118: expected 5 fields, saw 6
Skipping line 121: expected 5 fields, saw 6
Skipping line 124: expected 5 fields, saw 6
Skipping line 126: expected 5 fields, saw 6
Skipping line 128: expected 5 fields, saw 6
Skipping line 132: expected 5 fields, saw 6
Skipping line 134: expected 5 fields, saw 6
Skipping line 136: expected 5 fields, saw 6
Skipping line 138: expected 5 fields, saw 6
Skipping line 146: expected 5 fields, saw 6
Skipping line 148: expected 5 fields, sa

Analyzing commit  ccd4793215e78f1fa00a11596802d45a38cc4424  of  workcraft


Skipping line 11: expected 5 fields, saw 6
Skipping line 13: expected 5 fields, saw 6
Skipping line 15: expected 5 fields, saw 6
Skipping line 17: expected 5 fields, saw 6
Skipping line 19: expected 5 fields, saw 6
Skipping line 21: expected 5 fields, saw 6
Skipping line 27: expected 5 fields, saw 6
Skipping line 99: expected 5 fields, saw 6
Skipping line 109: expected 5 fields, saw 6
Skipping line 111: expected 5 fields, saw 6
Skipping line 119: expected 5 fields, saw 6
Skipping line 129: expected 5 fields, saw 6
Skipping line 132: expected 5 fields, saw 6
Skipping line 134: expected 5 fields, saw 6
Skipping line 136: expected 5 fields, saw 6
Skipping line 141: expected 5 fields, saw 6
Skipping line 145: expected 5 fields, saw 6
Skipping line 148: expected 5 fields, saw 6
Skipping line 151: expected 5 fields, saw 6
Skipping line 153: expected 5 fields, saw 6
Skipping line 155: expected 5 fields, saw 6
Skipping line 159: expected 5 fields, saw 6
Skipping line 161: expected 5 fields, sa

Analyzing commit  f0453ede75fe98fe7fb86341deb4baa8f146a257  of  workcraft


Skipping line 11: expected 5 fields, saw 6
Skipping line 13: expected 5 fields, saw 6
Skipping line 15: expected 5 fields, saw 6
Skipping line 17: expected 5 fields, saw 6
Skipping line 19: expected 5 fields, saw 6
Skipping line 21: expected 5 fields, saw 6
Skipping line 27: expected 5 fields, saw 6
Skipping line 97: expected 5 fields, saw 6
Skipping line 107: expected 5 fields, saw 6
Skipping line 109: expected 5 fields, saw 6
Skipping line 116: expected 5 fields, saw 6
Skipping line 126: expected 5 fields, saw 6
Skipping line 129: expected 5 fields, saw 6
Skipping line 131: expected 5 fields, saw 6
Skipping line 133: expected 5 fields, saw 6
Skipping line 138: expected 5 fields, saw 6
Skipping line 142: expected 5 fields, saw 6
Skipping line 145: expected 5 fields, saw 6
Skipping line 148: expected 5 fields, saw 6
Skipping line 150: expected 5 fields, saw 6
Skipping line 152: expected 5 fields, saw 6
Skipping line 156: expected 5 fields, saw 6
Skipping line 158: expected 5 fields, sa

In [172]:
imp_agg.to_csv('imp-agg-bug-fix.csv')
des_agg.to_csv('des-agg-bug-fix.csv')
arch_agg.to_csv('arch-agg-bug-fix.csv')

In [78]:
import os

fixed_path = os.path.join('data', 'mining','fixed', 'simulation')
inducing_path = os.path.join('data', 'mining','inducing', 'simulation')

imp_agg = pd.DataFrame(columns=['Project','Package', 'Type','Method', 'Smell','commit'])
des_agg = pd.DataFrame(columns=['Project','Package', 'Type', 'Smell', 'commit'])
arch_agg = pd.DataFrame(columns=['Project', 'Package', 'Smell', 'commit'])
type_agg = pd.DataFrame()
        
for repo in os.listdir(inducing_path):
    repo_path = os.path.join(inducing_path, repo)
    
    print("Analyzing repo ", repo)
    
    sub_imp_agg = pd.DataFrame(columns=['Project','Package', 'Type','Method', 'Smell', 'commit'])
    sub_des_agg = pd.DataFrame(columns=['Project','Package', 'Type', 'Smell', 'commit'])
    sub_arch_agg = pd.DataFrame(columns=['Project', 'Package', 'Smell', 'commit'])
    sub_type_agg = pd.DataFrame()
    
    for subfolder in os.listdir(repo_path):
        subfolder_path = os.path.join(repo_path, subfolder)
        
        if os.path.isdir(subfolder_path):
            commit = subfolder_path.split('_')[1]
            print('Analyzing commit ', commit, ' of ', repo)
            
            metrics_path = os.path.join(subfolder_path, 'TypeMetrics.csv')
            metrics = pd.read_csv(metrics_path, on_bad_lines='warn')
            metrics = metrics.drop_duplicates()
            metrics['commit'] = commit
            
            implementaion_path = os.path.join(subfolder_path, 'ImplementationSmells.csv')
            design_path = os.path.join(subfolder_path, 'DesignSmells.csv')
            arch_path = os.path.join(subfolder_path, 'ArchitectureSmells.csv')
            
            implementation = pd.read_csv(implementaion_path, on_bad_lines='warn')
            implementation = implementation.drop_duplicates()
            implementation = implementation.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Type Name': 'Type',
                'Method Name': 'Method',
                'Implementation Smell': 'Smell'
            })
            implementation['commit'] = commit;
            
            design = pd.read_csv(design_path, on_bad_lines='warn')
            design = design.drop_duplicates()
            
            design = design.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Type Name': 'Type',
                'Design Smell': 'Smell'
            })
            design['commit'] = commit;
            
            architecture = pd.read_csv(arch_path, on_bad_lines='warn')
            architecture = architecture.drop_duplicates()
            
            architecure = architecure.rename(columns={
                'Project Name': 'Project',
                'Package Name': 'Package',
                'Architecture Smell': 'Smell'
            })
            architecture['commit'] = commit;
            
            sub_imp_agg = pd.concat([sub_imp_agg, implementation])
            sub_des_agg = pd.concat([sub_des_agg, design])
            sub_arch_agg = pd.concat([sub_arch_agg, architecture])
            
            if sub_type_agg.empty:
                sub_type_agg = metrics
            else:
                sub_type_agg = pd.concat([sub_type_agg, metrics])
            
            sub_imp_agg = sub_imp_agg.drop_duplicates()
            sub_des_agg = sub_des_agg.drop_duplicates()
            sub_arch_agg = sub_arch_agg.drop_duplicates()
            

        imp_agg = pd.concat([sub_imp_agg, imp_agg])
        des_agg = pd.concat([sub_des_agg, des_agg])
        arch_agg = pd.concat([sub_arch_agg, arch_agg])
        if type_agg.empty:
            type_agg = sub_type_agg
        else:
            type_agg = pd.concat([sub_type_agg, type_agg])

Analyzing repo  adf-sample-agent-java
Analyzing commit  10e55eb8c686544c89ec25b9c277088ab931c6bd  of  adf-sample-agent-java
             Project Name                                  Package Name  \
0   adf-sample-agent-java               adf.sample.algorithm.clustering   
1   adf-sample-agent-java               adf.sample.algorithm.clustering   
2   adf-sample-agent-java             adf.sample.algorithm.pathplanning   
3   adf-sample-agent-java             adf.sample.complex.targetselector   
4   adf-sample-agent-java             adf.sample.complex.targetselector   
5   adf-sample-agent-java             adf.sample.complex.targetselector   
6   adf-sample-agent-java             adf.sample.complex.targetselector   
7   adf-sample-agent-java  adf.sample.complex.targetselector.clustering   
8   adf-sample-agent-java  adf.sample.complex.targetselector.clustering   
9   adf-sample-agent-java  adf.sample.complex.targetselector.clustering   
10  adf-sample-agent-java                          

Analyzing commit  ac2a1864c9fb4a745bebca2e095011a605335751  of  adf-sample-agent-java
             Project Name                       Package Name  \
0   adf-sample-agent-java    adf.sample.algorithm.clustering   
1   adf-sample-agent-java    adf.sample.algorithm.clustering   
2   adf-sample-agent-java  adf.sample.algorithm.pathplanning   
3   adf-sample-agent-java  adf.sample.complex.targetselector   
4   adf-sample-agent-java  adf.sample.complex.targetselector   
..                    ...                                ...   
18  adf-sample-agent-java            adf.sample.tactics.fire   
19  adf-sample-agent-java            adf.sample.tactics.fire   
20  adf-sample-agent-java          adf.sample.tactics.police   
21  adf-sample-agent-java          adf.sample.tactics.police   
22  adf-sample-agent-java                    adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  \
0           PathBasedKMeans   10     5   29    18  304   70   0    0   
1

             Project Name                                Package Name  \
0                   aerie  gov.nasa.jpl.aerie.banananation.activities   
1                   aerie  gov.nasa.jpl.aerie.banananation.activities   
2                   aerie  gov.nasa.jpl.aerie.banananation.activities   
3                   aerie  gov.nasa.jpl.aerie.banananation.activities   
4                   aerie  gov.nasa.jpl.aerie.banananation.activities   
..                    ...                                         ...   
18  adf-sample-agent-java                     adf.sample.tactics.fire   
19  adf-sample-agent-java                     adf.sample.tactics.fire   
20  adf-sample-agent-java                   adf.sample.tactics.police   
21  adf-sample-agent-java                   adf.sample.tactics.police   
22  adf-sample-agent-java                             adf.sample.util   

                             Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  \
0                             Defaults    1  

             Project Name                                Package Name  \
0                   aerie  gov.nasa.jpl.aerie.banananation.activities   
1                   aerie  gov.nasa.jpl.aerie.banananation.activities   
2                   aerie  gov.nasa.jpl.aerie.banananation.activities   
3                   aerie  gov.nasa.jpl.aerie.banananation.activities   
4                   aerie  gov.nasa.jpl.aerie.banananation.activities   
..                    ...                                         ...   
18  adf-sample-agent-java                     adf.sample.tactics.fire   
19  adf-sample-agent-java                     adf.sample.tactics.fire   
20  adf-sample-agent-java                   adf.sample.tactics.police   
21  adf-sample-agent-java                   adf.sample.tactics.police   
22  adf-sample-agent-java                             adf.sample.util   

                             Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  \
0                             Defaults    1  

             Project Name                                Package Name  \
0                   aerie  gov.nasa.jpl.aerie.banananation.activities   
1                   aerie  gov.nasa.jpl.aerie.banananation.activities   
2                   aerie  gov.nasa.jpl.aerie.banananation.activities   
3                   aerie  gov.nasa.jpl.aerie.banananation.activities   
4                   aerie  gov.nasa.jpl.aerie.banananation.activities   
..                    ...                                         ...   
18  adf-sample-agent-java                     adf.sample.tactics.fire   
19  adf-sample-agent-java                     adf.sample.tactics.fire   
20  adf-sample-agent-java                   adf.sample.tactics.police   
21  adf-sample-agent-java                   adf.sample.tactics.police   
22  adf-sample-agent-java                             adf.sample.util   

                             Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  \
0                             Defaults    1  

...

             Project Name                 Package Name  \
0               workcraft    org.workcraft.annotations   
1               workcraft  org.workcraft.binarymapping   
2               workcraft  org.workcraft.binarymapping   
3               workcraft  org.workcraft.binarymapping   
4               workcraft                org.workcraft   
..                    ...                          ...   
18  adf-sample-agent-java      adf.sample.tactics.fire   
19  adf-sample-agent-java      adf.sample.tactics.fire   
20  adf-sample-agent-java    adf.sample.tactics.police   
21  adf-sample-agent-java    adf.sample.tactics.police   
22  adf-sample-agent-java              adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  LCOM  \
0               Annotations    0     0   11    11   60   21   0    0  -1.0   
1              BinaryMapper    0     0    1     1    5    1   0    0  -1.0   
2                    BMNode    0     0    1     1    3    1   0    0 

             Project Name                 Package Name  \
0               workcraft    org.workcraft.annotations   
1               workcraft  org.workcraft.binarymapping   
2               workcraft  org.workcraft.binarymapping   
3               workcraft  org.workcraft.binarymapping   
4               workcraft                org.workcraft   
..                    ...                          ...   
18  adf-sample-agent-java      adf.sample.tactics.fire   
19  adf-sample-agent-java      adf.sample.tactics.fire   
20  adf-sample-agent-java    adf.sample.tactics.police   
21  adf-sample-agent-java    adf.sample.tactics.police   
22  adf-sample-agent-java              adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  LCOM  \
0               Annotations    0     0   11    11   60   21   0    0  -1.0   
1              BinaryMapper    0     0    1     1    5    1   0    0  -1.0   
2                    BMNode    0     0    1     1    3    1   0    0 

             Project Name                 Package Name  \
0               workcraft    org.workcraft.annotations   
1               workcraft  org.workcraft.binarymapping   
2               workcraft  org.workcraft.binarymapping   
3               workcraft  org.workcraft.binarymapping   
4               workcraft                org.workcraft   
..                    ...                          ...   
18  adf-sample-agent-java      adf.sample.tactics.fire   
19  adf-sample-agent-java      adf.sample.tactics.fire   
20  adf-sample-agent-java    adf.sample.tactics.police   
21  adf-sample-agent-java    adf.sample.tactics.police   
22  adf-sample-agent-java              adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  LCOM  \
0               Annotations    0     0   11    11   60   21   0    0  -1.0   
1              BinaryMapper    0     0    1     1    5    1   0    0  -1.0   
2                    BMNode    0     0    1     1    3    1   0    0 

             Project Name                 Package Name  \
0               workcraft    org.workcraft.annotations   
1               workcraft  org.workcraft.binarymapping   
2               workcraft  org.workcraft.binarymapping   
3               workcraft  org.workcraft.binarymapping   
4               workcraft                org.workcraft   
..                    ...                          ...   
18  adf-sample-agent-java      adf.sample.tactics.fire   
19  adf-sample-agent-java      adf.sample.tactics.fire   
20  adf-sample-agent-java    adf.sample.tactics.police   
21  adf-sample-agent-java    adf.sample.tactics.police   
22  adf-sample-agent-java              adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  LCOM  \
0               Annotations    0     0   11    11   60   21   0    0  -1.0   
1              BinaryMapper    0     0    1     1    5    1   0    0  -1.0   
2                    BMNode    0     0    1     1    3    1   0    0 

             Project Name                 Package Name  \
0               workcraft    org.workcraft.annotations   
1               workcraft  org.workcraft.binarymapping   
2               workcraft  org.workcraft.binarymapping   
3               workcraft  org.workcraft.binarymapping   
4               workcraft                org.workcraft   
..                    ...                          ...   
18  adf-sample-agent-java      adf.sample.tactics.fire   
19  adf-sample-agent-java      adf.sample.tactics.fire   
20  adf-sample-agent-java    adf.sample.tactics.police   
21  adf-sample-agent-java    adf.sample.tactics.police   
22  adf-sample-agent-java              adf.sample.util   

                  Type Name  NOF  NOPF  NOM  NOPM  LOC  WMC  NC  DIT  LCOM  \
0               Annotations    0     0   11    11   60   21   0    0  -1.0   
1              BinaryMapper    0     0    1     1    5    1   0    0  -1.0   
2                    BMNode    0     0    1     1    3    1   0    0 

In [24]:
imp_agg.to_csv('imp-agg-bug-ind.csv')
des_agg.to_csv('des-agg-bug-ind.csv')
arch_agg.to_csv('arch-agg-bug-ind.csv')

In [79]:
type_agg.to_csv('type-agg-bug-ind.csv')